In [4]:
using Plots
plotly()

Plots.PlotlyBackend()

# Flat distribution

In [1]:
const scalefactor = 1 / (1 + 0xFFFFFFFF)

function twiddle(var::UInt32)
    for i = 1:9
        var = xor(var, var << 13)
        var = xor(var, var >> 17)
        var = xor(var, var << 5)
    end
    
    var
end

mutable struct Flat128RNG <: AbstractRNG
    state::Array{UInt32}
end

function nextstate(state::Array{UInt32})
    tmp::UInt32 = xor(state[1], state[1] << 11)
    state[1] = state[2]
    state[2] = state[3]
    state[3] = state[4]
    state[4] = xor(xor(state[4], state[4] >> 19), xor(tmp, tmp >> 8))
    
    state
end

function initflatrng128(xstart = 123456789, ystart=362436069, zstart=521288629, wstart=88675123)
    rng = Flat128RNG(Array{UInt32}([xstart, ystart, zstart, wstart]))
    
    # Suffle the bits in the seeds
    for i = 1:4
        rng.state[i] = twiddle(rng.state[i])
    end
    
    # Burnin the RNG
    for i = 1:17
        rng.state = nextstate(rng.state)
    end
    
    rng
end

function Base.rand(rng::Flat128RNG)
    result = rng.state[4] * scalefactor
    nextstate(rng.state)
    result
end

In [2]:
ref = [0.9854981268, 0.2536861135,
       0.8791850018, 0.8541532028,
       0.4161281283, 0.6491611481,
       0.8336713058, 0.2541507778,
       0.0673349826, 0.7994472017,
       0.2600378725, 0.5134736516,
       0.4544143085, 0.9879117254,
       0.1875971474, 0.1698732623,
       0.9844831470, 0.2436698098,
       0.2365035815, 0.9442295933]

flatrng = initflatrng128()
for (idx, sample) in enumerate([rand(flatrng) for i = 1:length(ref)])
    @assert ref[idx] ≈ sample
end

In [5]:
flatrng = initflatrng128()
histogram([rand(flatrng) for i = 1:100000], leg=false)

# Gaussian generator

In [6]:
mutable struct GaussRNG
    flatrng
    empty::Bool
    gset
end

GaussRNG(flatrng::AbstractRNG) = GaussRNG(flatrng, true, 0)
GaussRNG(seed = 0) = GaussRNG(MersenneTwister(seed))

function Base.randn(state::GaussRNG)
    if state.empty
        local v1, v2, rsq
        
        while true
            v1 = 2 * rand(state.flatrng) - 1.0
            v2 = 2 * rand(state.flatrng) - 1.0
            rsq = v1^2 + v2^2
            if 0 < rsq < 1
                break
            end
        end
        
        fac = sqrt(-2log(rsq) / rsq)
        state.gset = v1 * fac
        state.empty = false
        
        v2 * fac
    else
        state.empty = true
        state.gset
    end
end

In [7]:
ref = [1.8051588123, -1.0150233503,
       -0.5138818361, 0.6974503387,
       0.0959640650, -1.7090943033,
       0.2825155379, -0.0263954840,
       -0.4486580098, -0.4245704031,
       -1.6567426564, -1.2158240845,
       0.3230971021, -1.0730251963,
       -0.6426576020, 1.0481948256,
       -0.0527193353, -0.2020275077,
       0.4885079587, 0.2111337896]

normrng = GaussRNG(initflatrng128())
for (idx, sample) in enumerate([randn(normrng) for i = 1:length(ref)])
    @assert ref[idx] ≈ sample
end

In [8]:
normrng = GaussRNG()
histogram([randn(normrng) for i=1:10000], leg=false)

In [10]:
normrng = GaussRNG(MersenneTwister(1234))
histogram([randn(normrng) for i=1:10000], leg=false)

# $1/f^2$ generator

In [27]:
mutable struct Oof2RNG
    normrng
    c0::Float64
    c1::Float64
    d0::Float64
    x1::Float64
    y1::Float64
end

function Oof2RNG(normrng, fmin::Number, fknee::Number, fsample::Number)
    w0 = π * fmin / fsample
    w1 = π * fknee / fsample
    
    Oof2RNG(normrng,
            (1.0 + w1) / (1.0 + w0),
            (w1 - 1.0) / (1.0 + w0),
            (1.0 - w0) / (1.0 + w0),
            0,
            0)
end

function oof2filter(rng::Oof2RNG, x2::Float64)
    y2 = rng.c0 * x2 + rng.c1 * rng.x1 + rng.d0 * rng.y1
    rng.x1 = x2
    rng.y1 = y2
    
    y2
end

randoof2(rng::Oof2RNG) = oof2filter(rng, randn(rng.normrng))

randoof2 (generic function with 1 method)

In [28]:
ref = [2.0886370365, -0.6074844495,
       -0.3464683356, 0.8936789422,
       0.4167745672, -1.6416294545,
       0.1259486772, -0.1427304943,
       -0.6395859847, -0.7526144784,
       -2.3116079175, -2.3217436788,
       -0.9229344940, -2.4367338428,
       -2.2756948201, -0.5210397131,
       -1.4655131788, -1.6547241628,
       -0.9190954646, -1.0864977062]

normrng = GaussRNG(initflatrng128())
oof2rng = Oof2RNG(normrng, 1.15e-5, 0.05, 1.0)
for (idx, sample) in enumerate([randoof2(oof2rng) for i = 1:length(ref)])
    @assert ref[idx] ≈ sample
end

In [31]:
oof2state = Oof2RNG(GaussRNG(), 1.15e-5, 0.05, 1.0)
data = [randoof2(oof2state) for i = 1:100000]
plot(data)

# $1/f^\alpha$ generator

In [41]:
mutable struct OofRNG
    normrng
    slope
    fmin
    fknee
    fsample
    oof2states::Array{Oof2RNG}
end

wminmax(fmin::Number, fknee::Number) = (log10(2π * fmin), log10(2π * fknee))

function numofpoles(fmin::Number, fknee::Number, fsample::Number)
    (wmin, wmax) = wminmax(fmin, fknee)
    
    convert(Int32, floor(2(wmax - wmin) + log10(fsample)))
end

const OOF2STATESIZE = 5
oofstatesize(fmin::Number, fknee::Number, fsample::Number) = OOF2STATESIZE * numofpoles(fmin, fknee, fsample)

function OofRNG(normrng, slope::Number, fmin::Number, fknee::Number, fsample::Number)
    (wmin, wmax) = wminmax(fmin, fknee)
    a = -slope
    nproc = numofpoles(fmin, fknee, fsample)
    dp = (wmax - wmin) / nproc
    
    p = wmin + (1 - a/2) * dp / 2
    z = p + a * dp / 2
    
    oof2states = Array{Oof2RNG}(nproc)
    for i = 1:nproc
        oof2states[i] = Oof2RNG(normrng, 10^p / (2π), 10^z / (2π), fsample)
        
        p += dp
        z = p + a * dp / 2
    end
    
    OofRNG(normrng, slope, fmin, fknee, fsample, oof2states)
end

function randoof(rng::OofRNG)
    x2 = randn(rng.normrng)
    for curstate in rng.oof2states
        x2 = oof2filter(curstate, x2)
    end
    
    x2
end

randoof (generic function with 1 method)

In [42]:
ref = [2.0400958027, -0.6813881047,
       -0.3848671621, 0.84863765610,
       0.34838982440, -1.6703162833,
       0.13588215630, -0.1362109745,
       -0.6176813736, -0.7037434318,
       -2.2015645097, -2.1249009577,
       -0.6866971017, -2.1640479726,
       -1.9400718236, -0.1768193407,
       -1.1308790625, -1.2995275170,
       -0.5582322798, -0.7326164277]

normrng = GaussRNG(initflatrng128())
oofrng = OofRNG(normrng, -1.7, 1.15e-5, 0.05, 1.0)
for (idx, sample) in enumerate([randoof(oofrng) for i = 1:length(ref)])
    @assert ref[idx] ≈ sample
end

In [46]:
oofstate = OofRNG(MersenneTwister(0), -1.7, 1.15e-5, 0.05, 1.0)
data = [randoof(oofstate) for i = 1:100000]
plot(data)